In [1]:
import pandas as pd
import numpy as np
import yaml
from sklearn.manifold import TSNE
from sklearn.cluster import DBSCAN
from scipy.fft import fft
from scipy.stats import boxcox
from scipy.special import inv_boxcox
import matplotlib.pyplot as plt
from plotly.subplots import make_subplots
from sklearn.preprocessing import StandardScaler, OneHotEncoder, LabelEncoder, MinMaxScaler, PowerTransformer, RobustScaler
import openpyxl
import plotly.graph_objects as go
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score, recall_score,precision_score, f1_score, mean_squared_error
import xgboost as xgb
import optuna
import talib
import json
import pickle


/Users/rahuladmin/GIT/Uns_SPY_Trading/venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def load_yaml(file):
    import yaml
    with open(file, 'r') as f:
        config = yaml.safe_load(f)
    return config
    



In [3]:
config = load_yaml('../config_Reg.yaml')

In [4]:
#trading_data = pd.read_excel(config['data_excel_path'], sheet_name='Data_Basic')
#trading_data.count()
all_trading_data_dfs = []
sheet_names = ['5minData11-6-2014', '5minData12-17-2019']
for sheet in sheet_names:
    temp_df = pd.read_excel(config['all_data_excel_path'], sheet_name=sheet)
    all_trading_data_dfs.append(temp_df)
all_trading_data = pd.concat(all_trading_data_dfs, ignore_index=True)

# Load 5 min data
all_trading_data['Date'] = pd.to_datetime(all_trading_data['Date'])


In [5]:
##### Set the Date Start and End for the filtering of trading data

train_start_date = pd.to_datetime(config['train_start_date'])
train_end_date = pd.to_datetime(config['train_end_date'])

trading_data_raw = all_trading_data[(all_trading_data['Date'] >= train_start_date) & (all_trading_data['Date'] <= train_end_date)]
trading_data_raw = trading_data_raw.reset_index(drop=True)
trading_data_raw.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19430 entries, 0 to 19429
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   Date    19430 non-null  datetime64[ns]
 1   Symbol  19430 non-null  object        
 2   Open    19430 non-null  float64       
 3   High    19430 non-null  float64       
 4   Low     19430 non-null  float64       
 5   Close   19430 non-null  float64       
 6   Volume  19430 non-null  int64         
dtypes: datetime64[ns](1), float64(4), int64(1), object(1)
memory usage: 1.0+ MB


In [6]:
def calculate_bollinger_bands(data, window_size, num_std_dev):
    rolling_mean = data['Close'].rolling(window=window_size).mean()
    rolling_std = data['Close'].rolling(window=window_size).std()
    data['BOLLBU'] = rolling_mean + (rolling_std * num_std_dev)
    data['BOLLBM'] = rolling_mean
    data['BOLLBL'] = rolling_mean - (rolling_std * num_std_dev)
    
    return data

def calculate_donchn_bands(data, window_size):
    data['DONCH_U'] = data['High'].rolling(window=window_size).max()
    data['DONCH_L'] = data['Low'].rolling(window=window_size).min()
    
    return data
    
def calculate_tchr(data):
    period = config['tchr_period']
    retracement = config['tchr_retracement']
    adj = config['tchr_adj']
    range = config['tchr_range']

    if range == 'highlow':
        data['TCHR_U'] = talib.MAX(data['High'], timeperiod=period) + adj
        data['TCHR_L'] = talib.MIN(data['Low'], timeperiod=period) - adj
    elif range == 'close':
        data['TCHR_U'] = talib.MAX(data['Close'], timeperiod=period) + adj
        data['TCHR_L'] = talib.MIN(data['Close'], timeperiod=period) - adj
    
    #calculate retracement
    if retracement == "long":
        data['TCHR'] = (data['Close'] - data['TCHR_L']) / (data['TCHR_U'] - data['TCHR_L'])
    elif retracement == "short":
        data['TCHR'] = (data['TCHR_U'] - data['Close']) / (data['TCHR_U'] - data['TCHR_L'])
    
    return data
    
def calculate_adwm(data):
    period = config['adwm_period']
    data['Previous_Close']= data['Close'].shift(1)
    data['TRH'] = data[['High', 'Previous_Close']].max(axis=1)
    data['TRL'] = data[['Low', 'Previous_Close']].min(axis=1)

    data['ADWM_AD'] = 0.0
    data.loc[data['Close'] > data['Previous_Close'], 'ADWM_AD'] = (data['Close'] - data['TRL'])
    data.loc[data['Close'] < data['Previous_Close'], 'ADWM_AD'] = (data['Close'] - data['TRH'])

    data['ADWM'] = data['ADWM_AD']

    data['ADWMMA'] = data['ADWM'].rolling(window=period).mean()

    return data

def calculate_si(row, prev_row, limit):
    if pd.isna(prev_row['Close']):
        return 0
    c = row['Close']
    c_prev = prev_row['Close']
    o = row['Open']
    o_prev = prev_row['Open']
    return (50 * ((c - c_prev) + (0.5 * (c - o)) + (0.25 * (c_prev - o_prev))) / limit)

def calculate_WASI(data):
    wasi_limit = config['wasi_limit']
    data['SI'] = data.apply(lambda row: calculate_si(row, data.shift(1).loc[row.name], wasi_limit), axis=1)
    data['WASI'] = data['SI']
    return data

def calculate_ATR(data):
    atr_period = config['atr_period']
    atr_ma = config['atr_ma']
    data['ATR'] = talib.ATR(data['High'], data['Low'], data['Close'], timeperiod=atr_period)
    data['ADJATR'] = talib.SMA(data['ATR'], timeperiod=atr_ma)
    return data


def compute_fourier_df(value_series, n_components=10):
    fft_result = np.fft.fft(value_series)
    real = fft_result.real[:n_components]
    imag = fft_result.imag[:n_components]
    mag = np.abs(fft_result)[:n_components]

    return real, imag, mag

    

In [7]:
fourier_lookback_window = config['fourier_lookback_window']
fourier_n_components = config['fourier_n_components']
raw_features_g1 = config['raw_features_g1'].split(',')

#g2 is the other features. need to use standard scaler for this
raw_features_g2 = config['raw_features_g2'].split(',')

#g3 is volume features. need to use min max scaler separately
raw_features_g3 = config['raw_features_g3'].split(',')

raw_features_g4 = config['raw_features_g4'].split(',')

In [8]:
def add_new_features_df(data):
    global fourier_lookback_window
    global fourier_n_components
    global raw_features_g1
    global raw_features_g2
    global raw_features_g3
    global raw_features_g4
    data['Date'] = pd.to_datetime(data['Date'])
    #print(f"bolband period : {config['bolband_period']}")
    bolband_period = config['bolband_period']
    bolband_width = config['bolband_width']
    upper, middle, lower = talib.BBANDS(data['Close'], timeperiod=bolband_period, nbdevup=bolband_width, nbdevdn=bolband_width, matype=0)
    data['BOLLBU'] = upper
    data['BOLLBM'] = middle
    data['BOLLBL'] = lower
    #data = calculate_bollinger_bands(data, int(config['bolband_period']), int(config['bolband_width']))

    # Calculate DONCHN Bands
    donchn_period = config['donchn_period']
    data['DONUP'] = talib.MAX(data['High'], timeperiod=donchn_period)

    data['DONLOW'] = talib.MIN(data['Low'], timeperiod=donchn_period)

    data['DONMID'] = (data['DONLOW'] + data['DONUP']) / 2

    data['MA20'] = talib.SMA(data['Close'], timeperiod=20)

    data['MA50'] = talib.SMA(data['Close'], timeperiod=50)

    data['MA100'] = talib.SMA(data['Close'], timeperiod=100)

    data['EMA20'] = talib.EMA(data['Close'], timeperiod=20)

    # Calculate the pivot points
    data['PVPT'] = (data['High'] + data['Low'] + data['Close']) / 3
    data['PVPTR1'] = (2 * data['PVPT']) - data['Low']

    data['PVPTR2'] = data['PVPT'] + data['High'] - data['Low']

    data['PVPTR3'] = data['High'] + 2 * (data['PVPT'] - data['Low'])

    data['PVPTS1'] = (2 * data['PVPT']) - data['High']

    data['PVPTS2'] = data['PVPT'] + data['High'] - data['Low']

    data['PVPTS3'] = data['Low'] - 2 * (data['High'] - data['PVPT'])

    data = calculate_tchr(data)

    data = calculate_adwm(data)

    data = calculate_WASI(data)

    volume_ma_period = config['volume_ma_period']

    data['VOLMA'] = talib.SMA(data['Volume'], timeperiod=volume_ma_period)

    data = calculate_ATR(data)

    data['DayofWeek'] = data['Date'].dt.dayofweek

    data['DayofWeek'] = data['DayofWeek'].astype('category')

    # Add fourier columns to the df
    for i in range(fourier_n_components):
        data[f'fourier_real_{i+1}'] = np.nan
        data[f'fourier_imag_{i+1}'] = np.nan
        data[f'fourier_mag_{i+1}'] = np.nan

    features = []
    epsilon = 1e-5
    #print(f"fourier window - 1 : {fourier_lookback_window - 1}")
    for i in range(len(data)):
        if i >= fourier_lookback_window - 1:
            #print("entered point 1")
            close_window = data['Close'].iloc[i - fourier_lookback_window + 1: i + 1].values
            real, imag, mag = compute_fourier_df(close_window, n_components=fourier_n_components)

            for j in range(fourier_n_components):
                data.loc[i, f'fourier_real_{j+1}'] = real[j]
                data.loc[i, f'fourier_imag_{j+1}'] = imag[j]
                data.loc[i, f'fourier_mag_{j+1}'] = mag[j]
    
    # Apply min max scaling to the fouorier columns separately for real, imag and mag 
    #real_cols = [col for col in data.columns if col.startswith("fourier_real")]
    #imag_cols = [col for col in data.columns if col.startswith("fourier_imag")]
    #mag_cols = [col for col in data.columns if col.startswith("fourier_mag")]



    # Add the time of day feature to the trading data

    # Define max time of day in minutes
    MAX_TIME_MINUTES = 1440
    data['Minutes_Passed'] = (data['Date'].dt.hour* 60) + data['Date'].dt.minute
    #invalid_Rows = data[data['Minutes_Passed'].isna() | data['Minutes_Passed'].isin([np.inf, -np.inf])]
    #print(f"Invalid rows count : {invalid_Rows.shape[0]}")
    #print(invalid_Rows.head(10))
    data['TimeOfDay_Group'] = (data['Minutes_Passed'] // 5).astype('int')
    data['Sine_TimeOfDay'] = np.sin(2 * np.pi * data['TimeOfDay_Group'] / MAX_TIME_MINUTES)
    data['Cosine_TimeOfDay'] = np.cos(2 * np.pi * data['TimeOfDay_Group'] / MAX_TIME_MINUTES)
    data['Take_Profit_Level'] = (data['Close'] * config['atr_multiplier'] * data['ADJATR'])
    #print(f"Last row after adding features : ")
    #print(data.tail())
    return data


In [9]:

def calculate_label2(data):

# Define the threshold for buy and sell signals
    
    buy_powers = []
    sell_powers = []
    n=config['bars_no_to_wait']
    for i in range(len(data)):
        current_close = data.loc[i, "Close"]

        future_closes = data.loc[i+1: i+n+1, "Close"].values

        if len(future_closes) == 0:
            buy_powers.append(0)
            sell_powers.append(0)
            continue
        future_close_max = max(future_closes) 
        future_close_min = min(future_closes)
        max_high = future_close_max - current_close
        min_high = current_close - future_close_min
        max_high_idx = list(future_closes).index( future_close_max)
        min_high_idx = list(future_closes).index( future_close_min)

        if max_high_idx == (len(future_closes) - 1): #when max value is at the last of window
            buy_retr_penalty = 0
        else:
            buy_retr_penalty = future_close_max - min(future_closes[max_high_idx+1:])
        max_down_below = max(0, current_close - future_close_min)
        penalty_buy = buy_retr_penalty + max_down_below
        buy_power = max(0, max_high - penalty_buy)

        if min_high_idx == (len(future_closes) - 1): 
            sell_retr_penalty = 0
        else:
            sell_retr_penalty = max(future_closes[min_high_idx+1:]) - future_close_min
        max_up_above = max(0, future_close_max - current_close)
        penalty_sell = sell_retr_penalty + max_up_above
        sell_power = max(0, min_high - penalty_sell)

        buy_powers.append(buy_power)
        sell_powers.append(sell_power)

    data['BuyPower'] = buy_powers
    data['SellPower'] = sell_powers
        

    return data




In [10]:

def calculate_label(data):

# Define the threshold for buy and sell signals
    buy_penalties = []
    sell_penalties = []

    max_highs = []
    min_lows = []
    n=config['bars_no_to_wait']

    for i in range(len(data)):
        forward_window = data.iloc[i+1:n+i+1]

        if len(forward_window) < n:
            max_highs.append(np.nan)
            min_lows.append(np.nan)
            buy_penalties.append(np.nan)
            sell_penalties.append(np.nan)
            continue
        
        max_high = forward_window['Close'].max()
        min_low = forward_window['Close'].min()



        buy_penalty = 0
        sell_penalty = 0
        prev_close = data.iloc[i]['Close']

        for j in range(len(forward_window)):
            current_close = forward_window.iloc[j]['Close']

            if current_close < prev_close:
                buy_penalty += (prev_close - current_close)
            elif current_close > prev_close:
                sell_penalty += (current_close - prev_close)

            prev_close = current_close
        max_high = max(0, max_high - data.iloc[i]['Close'])
        min_low = max(0, data.iloc[i]['Close'] - min_low)
        max_highs.append(max_high)
        min_lows.append(min_low)
        buy_penalties.append(buy_penalty)
        sell_penalties.append(sell_penalty)

    data['Max_High_N'] = max_highs
    data['Min_Low_N'] = min_lows
    data['Buy_Penalty'] = buy_penalties
    data['Sell_Penalty'] = sell_penalties

    # Scale penalties to avoid extreme scaled values
    max_buy_penalty = max(abs(data['Buy_Penalty'].max()),1)
    max_sell_penalty = max(abs(data['Sell_Penalty'].max()),1)

    data['Scaled_Buy_Penalty'] = data['Buy_Penalty'] / max_buy_penalty * (data['Max_High_N'])
    data['Scaled_Sell_Penalty'] = data['Sell_Penalty'] / max_sell_penalty * (data['Min_Low_N'])
    
    # Reduce penalty from buy power and sell power
    data['BuyPower'] = data['Max_High_N'] - data['Scaled_Buy_Penalty']
    data['SellPower'] = data['Min_Low_N'] - data['Scaled_Sell_Penalty']

    scaler = MinMaxScaler(feature_range=(0,1))
    data['BuyPower'] = scaler.fit_transform(data[['BuyPower']])
    data['SellPower'] = scaler.fit_transform(data[['SellPower']])

    if config['label_power_transform']:
        pt = PowerTransformer(method='yeo-johnson')

        label_columns = ['BuyPower', 'SellPower']
        data[label_columns] = pt.fit_transform(data[label_columns])

        # Scale buy power and sell power to be in range 0 to 1 
        scaler = MinMaxScaler(feature_range=(0,1))
        data['BuyPower_Scaled'] = scaler.fit_transform(data[['BuyPower']])
        data['SellPower_Scaled'] = scaler.fit_transform(data[['SellPower']])

        label_scales = {'PT': pt, 'MinMax': scaler}
        with open(f'../{config['label_scales_pickle']}', 'wb') as f:
            pickle.dump(label_scales, f)
    else:
        data['BuyPower_Scaled'] = data['BuyPower']
        data['SellPower_Scaled'] = data['SellPower']

    return data




In [11]:
trading_data = add_new_features_df(trading_data_raw.copy())
trading_data = trading_data.dropna()
trading_data.reset_index(drop=True, inplace=True)

In [12]:

trading_data = calculate_label2(trading_data)
#trading_data['Label'] = trading_data['Label'].astype('category')

In [13]:
pd.set_option("display.max_columns", None)  # Show all columns
pd.set_option("display.max_rows", None)  # Show all rows
trading_data.describe().T

count                           mean  \
Date                 19331  2023-07-03 13:51:05.754487552   
Open               19331.0                     427.431208   
High               19331.0                     427.660784   
Low                19331.0                     427.197122   
Close              19331.0                     427.434626   
Volume             19331.0                  748786.948114   
BOLLBU             19331.0                      428.52629   
BOLLBM             19331.0                     427.388852   
BOLLBL             19331.0                     426.251414   
DONUP              19331.0                     428.537642   
DONLOW             19331.0                     426.174998   
DONMID             19331.0                      427.35632   
MA20               19331.0                     427.388852   
MA50               19331.0                     427.315981   
MA100              19331.0                     427.192698   
EMA20              19331.0                     427.388814   
PVPT               19331.0                     427.430844   
PVPTR1             19331.0                     427.664566   
PVPTR2             19331.0                     427.894506   
PVPTR3             19331.0                     428.128228   
PVPTS1             19331.0                     427.200904   
PVPTS2             19331.0                     427.894506   
PVPTS3             19331.0                     426.737242   
TCHR_U             19331.0                     434.999892   
TCHR_L             19331.0                     419.265148   
TCHR               19331.0                       0.518277   
Previous_Close     19331.0                      427.42987   
TRH                19331.0                     427.668187   
TRL                19331.0                     427.188433   
ADWM_AD            19331.0                       0.008094   
ADWM               19331.0                       0.008094   
ADWMMA             19331.0                       0.008207   
SI                 19331.0                       0.122008   
WASI               19331.0                       0.122008   
VOLMA              19331.0                  748081.370446   
ATR                19331.0                       0.480034   
ADJATR             19331.0                       0.480334   
fourier_real_1     19331.0                   42719.269845   
fourier_imag_1     19331.0                            0.0   
fourier_mag_1      19331.0                   42719.269845   
fourier_real_2     19331.0                      -0.310788   
fourier_imag_2     19331.0                       7.850098   
fourier_mag_2      19331.0                      72.320793   
fourier_real_3     19331.0                      -0.248039   
fourier_imag_3     19331.0                       3.919515   
fourier_mag_3      19331.0                      37.362643   
fourier_real_4     19331.0                        -0.2457   
fourier_imag_4     19331.0                       2.597581   
fourier_mag_4      19331.0                      24.507666   
fourier_real_5     19331.0                      -0.246092   
fourier_imag_5     19331.0                       1.949369   
fourier_mag_5      19331.0                      17.585356   
fourier_real_6     19331.0                      -0.247339   
fourier_imag_6     19331.0                       1.554989   
fourier_mag_6      19331.0                      14.444335   
fourier_real_7     19331.0                      -0.245908   
fourier_imag_7     19331.0                       1.291054   
fourier_mag_7      19331.0                       12.33056   
fourier_real_8     19331.0                      -0.246713   
fourier_imag_8     19331.0                       1.098958   
fourier_mag_8      19331.0                      10.656223   
fourier_real_9     19331.0                      -0.245147   
fourier_imag_9     19331.0                       0.955721   
fourier_mag_9      19331.0                       9.334925   
fourier_real_10    19331.0                      -0.24490

In [14]:

trading_data[trading_data['SellPower'] > 2].shape[0]

696

In [15]:
#trading_data['Date'] = pd.to_datetime(trading_data['Date'])
fig = go.Figure(data=[go.Candlestick(x=trading_data['Date'], open=trading_data['Open'], high=trading_data['High'], low=trading_data['Low'], close=trading_data['Close'])])
fig.update_layout(title='CandleStick Chart SPY', xaxis_title='Date', yaxis_title='Price', xaxis_rangeslider_visible=False, yaxis=dict(fixedrange=False), xaxis=dict(type='category'))
buy_signals = trading_data[trading_data['BuyPower'] > 2]
sell_signals = trading_data[trading_data['SellPower'] > 2]
fig.add_trace(go.Scatter(x=buy_signals['Date'], y=buy_signals['Low'], mode='markers', name='Buy Signal', marker=dict(color='blue', size=10)))
fig.add_trace(go.Scatter(x=sell_signals['Date'], y=sell_signals['High'], mode='markers', name='Sell Signal', marker=dict(color='yellow', size=10)))
fig.show()

In [16]:
def get_fourier_columns():
    return [f'fourier_real_{j+2}' for j in range(fourier_n_components-1)] + [f'fourier_imag_{j+2}' for j in range(fourier_n_components-1)] + [f'fourier_mag_{j+2}' for j in range(fourier_n_components-1)]   


In [17]:

def get_features(data, inference=False, scalers={}):
    
    # Define global variables
    global stand_scaler
    global raw_features_g1
    global raw_features_g2
    global raw_features_g3
    global raw_features_g4

    stand_features = config['stand_scale_features'].split(',')
    stand_features = [x for x in stand_features if x.strip()]
    robust_features = config['robust_scale_features'].split(',')
    robust_features = [x for x in robust_features if x.strip()]
    fourier_columns = get_fourier_columns()
    # need to use min max scaler for g1
    stand_features = stand_features + fourier_columns

    real_cols = [f'fourier_real_{j+2}' for j in range(fourier_n_components-1)]
    imag_cols = [f'fourier_imag_{j+2}' for j in range(fourier_n_components-1)]
    mag_cols = [f'fourier_mag_{j+2}' for j in range(fourier_n_components-1)]

    if inference:
        scaler = scalers['fourier_minmax']
        real_min, real_max = scaler['real_min'], scaler['real_max']
        imag_min, imag_max = scaler['imag_min'], scaler['imag_max']
        mag_min, mag_max = scaler['mag_min'], scaler['mag_max']

    else:
        real_min, real_max = data[real_cols].min().min(), data[real_cols].max().max()
        imag_min, imag_max = data[imag_cols].min().min(), data[imag_cols].max().max()
        mag_min, mag_max = data[mag_cols].min().min(), data[mag_cols].max().max()
        fourier_min_max = {
                    'real_min': real_min, 'real_max': real_max,
                    'imag_min': imag_min, 'imag_max': imag_max,
                    'mag_min': mag_min,'mag_max': mag_max,
                    }
        with open(f'../{config['fourier_minmax_path']}', 'wb') as f:
            pickle.dump(fourier_min_max, f)
    
    
    data[real_cols] = (data[real_cols] - real_min) / (real_max - real_min)
    data[imag_cols] = (data[imag_cols] - imag_min) / (imag_max - imag_min)
    data[mag_cols] = (data[mag_cols] - mag_min) / (mag_max - mag_min)

    # Apply standard scaler to g2
    #print("Before standard scaler")
    if inference:
        scaler = scalers['stand']
        data[stand_features] = scaler.transform(data[stand_features])
    else:
        scaler = StandardScaler()
        data[stand_features] = scaler.fit_transform(data[stand_features])
        #print("After standard scaler")

        with open(f'../{config['stand_scaler_path']}', 'wb') as f:
            pickle.dump(scaler, f)
    

    # Apply robust scaler
    if inference:
        scaler = scalers['robust']
        data[robust_features] = scaler.transform(data[robust_features])

    else:
        scaler = RobustScaler()
        data[robust_features] = scaler.fit_transform(data[robust_features])

        with open(f'../{config['robust_scaler_path']}', 'wb') as f:
            pickle.dump(scaler, f)
  

    return data


In [18]:
fourier_columns = get_fourier_columns()

#all_feature_columns = raw_features_g1 + raw_features_g2 + raw_features_g3 + raw_features_g4 + fourier_columns + ['DayofWeek']
#all_feature_columns = raw_features_g1 + raw_features_g2 + raw_features_g3 + raw_features_g4 + fourier_columns
all_feature_columns = raw_features_g1 + raw_features_g2 + raw_features_g3 + fourier_columns

print(all_feature_columns)


['Open', 'High', 'Low', 'Close', 'BOLLBU', 'BOLLBM', 'BOLLBL', 'DONUP', 'DONMID', 'DONLOW', 'MA20', 'MA50', 'MA100', 'EMA20', 'PVPTR1', 'PVPTR2', 'PVPTR3', 'PVPT', 'PVPTS1', 'PVPTS2', 'PVPTS3', 'ADWM', 'ADWMMA', 'WASI', 'ADJATR', 'TCHR', 'Volume', 'VOLMA', 'fourier_real_2', 'fourier_real_3', 'fourier_real_4', 'fourier_real_5', 'fourier_real_6', 'fourier_real_7', 'fourier_real_8', 'fourier_real_9', 'fourier_real_10', 'fourier_imag_2', 'fourier_imag_3', 'fourier_imag_4', 'fourier_imag_5', 'fourier_imag_6', 'fourier_imag_7', 'fourier_imag_8', 'fourier_imag_9', 'fourier_imag_10', 'fourier_mag_2', 'fourier_mag_3', 'fourier_mag_4', 'fourier_mag_5', 'fourier_mag_6', 'fourier_mag_7', 'fourier_mag_8', 'fourier_mag_9', 'fourier_mag_10']


In [19]:
trading_data_scaled = get_features(trading_data.copy())
trading_data_scaled = trading_data_scaled.dropna()
#trading_features = trading_data_full[all_feature_columns]
#trading_labels = trading_data_full['Label']

In [20]:
print(trading_data_scaled[all_feature_columns].shape)

(19331, 55)


In [21]:
trading_data_scaled.describe().T

count                           mean  \
Date                 19331  2023-07-03 13:51:05.754487552   
Open               19331.0                      -0.031253   
High               19331.0                      -0.031078   
Low                19331.0                      -0.029725   
Close              19331.0                      -0.031177   
Volume             19331.0                       0.415354   
BOLLBU             19331.0                      -0.029695   
BOLLBM             19331.0                      -0.030019   
BOLLBL             19331.0                      -0.035452   
DONUP              19331.0                      -0.029817   
DONLOW             19331.0                      -0.035431   
DONMID             19331.0                      -0.031381   
MA20               19331.0                      -0.030019   
MA50               19331.0                      -0.030885   
MA100              19331.0                      -0.025106   
EMA20              19331.0                      -0.029309   
PVPT               19331.0                      -0.030568   
PVPTR1             19331.0                      -0.030299   
PVPTR2             19331.0                      -0.030778   
PVPTR3             19331.0                      -0.030791   
PVPTS1             19331.0                      -0.030362   
PVPTS2             19331.0                      -0.030778   
PVPTS3             19331.0                      -0.030107   
TCHR_U             19331.0                     434.999892   
TCHR_L             19331.0                     419.265148   
TCHR               19331.0                      -0.035536   
Previous_Close     19331.0                      427.42987   
TRH                19331.0                     427.668187   
TRL                19331.0                     427.188433   
ADWM_AD            19331.0                       0.008094   
ADWM               19331.0                      -0.110537   
ADWMMA             19331.0                      -0.038252   
SI                 19331.0                       0.122008   
WASI               19331.0                      -0.023564   
VOLMA              19331.0                       0.351417   
ATR                19331.0                       0.480034   
ADJATR             19331.0                        0.18089   
fourier_real_1     19331.0                   42719.269845   
fourier_imag_1     19331.0                            0.0   
fourier_mag_1      19331.0                   42719.269845   
fourier_real_2     19331.0                            0.0   
fourier_imag_2     19331.0                           -0.0   
fourier_mag_2      19331.0                           -0.0   
fourier_real_3     19331.0                           -0.0   
fourier_imag_3     19331.0                           -0.0   
fourier_mag_3      19331.0                           -0.0   
fourier_real_4     19331.0                            0.0   
fourier_imag_4     19331.0                           -0.0   
fourier_mag_4      19331.0                           -0.0   
fourier_real_5     19331.0                           -0.0   
fourier_imag_5     19331.0                           -0.0   
fourier_mag_5      19331.0                           -0.0   
fourier_real_6     19331.0                            0.0   
fourier_imag_6     19331.0                           -0.0   
fourier_mag_6      19331.0                           -0.0   
fourier_real_7     19331.0                            0.0   
fourier_imag_7     19331.0                           -0.0   
fourier_mag_7      19331.0                            0.0   
fourier_real_8     19331.0                           -0.0   
fourier_imag_8     19331.0                            0.0   
fourier_mag_8      19331.0                            0.0   
fourier_real_9     19331.0                            0.0   
fourier_imag_9     19331.0                           -0.0   
fourier_mag_9      19331.0                            0.0   
fourier_real_10    19331.0                            0.

In [22]:

label_column_names = ['BuyPower', 'SellPower']
#assert trading_features.shape[0] == trading_labels.shape[0], "Mismatch between features and labels length"
X = trading_data_scaled[all_feature_columns]
y = trading_data_scaled[label_column_names]
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.3, random_state=46)
X_valid, X_test, y_valid, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=46)


In [23]:


#convert data to d matrix to use with xgb
enab_cat = True
dtrain = xgb.DMatrix(X_train, label=y_train, enable_categorical=enab_cat )
dvalid = xgb.DMatrix(X_valid, label=y_valid, enable_categorical=enab_cat)
dtest = xgb.DMatrix(X_test, label=y_test, enable_categorical=True)
dtrain_valid = xgb.DMatrix(data = pd.concat([X_train, X_valid]),label=pd.concat([y_train, y_valid]), enable_categorical=enab_cat)



In [24]:
num_boosting_rounds = config['num_boosting_rounds']

In [25]:

##### Implement initial training of the model   
learning_rate = 0.3
starting_tree_method = 'approx'
#metric can be mlogloss, auc, merror etc
metric = 'rmse'

base_params = {
    'objective': 'reg:squarederror',
    'eval_metric': metric
}

params = {
    'learning_rate': learning_rate,
    'tree_method': starting_tree_method
}

params.update(base_params)

model = xgb.train(params=params, dtrain=dtrain, num_boost_round=num_boosting_rounds, evals=[(dtrain, 'train')], early_stopping_rounds=50)

[0]	train-rmse:0.65146
[1]	train-rmse:0.63143
[2]	train-rmse:0.61183
[3]	train-rmse:0.59659
[4]	train-rmse:0.58424
[5]	train-rmse:0.57407
[6]	train-rmse:0.56223
[7]	train-rmse:0.55423
[8]	train-rmse:0.54807
[9]	train-rmse:0.53705
[10]	train-rmse:0.52679
[11]	train-rmse:0.51649
[12]	train-rmse:0.50514
[13]	train-rmse:0.49964
[14]	train-rmse:0.49080
[15]	train-rmse:0.48599
[16]	train-rmse:0.47881
[17]	train-rmse:0.46988
[18]	train-rmse:0.46425
[19]	train-rmse:0.45850
[20]	train-rmse:0.45153
[21]	train-rmse:0.44565
[22]	train-rmse:0.43752
[23]	train-rmse:0.43306
[24]	train-rmse:0.42766
[25]	train-rmse:0.42473
[26]	train-rmse:0.42167
[27]	train-rmse:0.41224
[28]	train-rmse:0.40571
[29]	train-rmse:0.40154
[30]	train-rmse:0.39686
[31]	train-rmse:0.39353
[32]	train-rmse:0.39074
[33]	train-rmse:0.38509
[34]	train-rmse:0.37983
[35]	train-rmse:0.37691
[36]	train-rmse:0.37462
[37]	train-rmse:0.37056
[38]	train-rmse:0.36737
[39]	train-rmse:0.36318
[40]	train-rmse:0.35607
[41]	train-rmse:0.35222
[4

In [26]:
##### CReate the objective function for optuna to tune tree parameters

def objective(trial):
    params = {
        'tree_method' : trial.suggest_categorical('tree_method', ['approx', 'hist']) , 
        'gamma': trial.suggest_float('gamma', 1e-2, 10),
        'max_depth': trial.suggest_int('max_depth', 3, 12),
        'min_child_weight': trial.suggest_float('min_child_weight', 1, 250),
        'subsample': trial.suggest_float('subsample', 0.1, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'lambda': trial.suggest_float('lambda', 0.1, 25), 
        'alpha': trial.suggest_float('alpha', 0.001, 10),
    }
    params.update(base_params)
    #thresholds = [trial.suggest_float(f'threshold_{i}', 0.1, 0.9) for i in ]
    pruning_callback = optuna.integration.XGBoostPruningCallback(trial, f'valid-{metric}')

    xgb_model = xgb.train(params=params, dtrain=dtrain, num_boost_round=num_boosting_rounds, 
                          evals=[(dtrain, 'train'),(dvalid, 'valid')],
                          early_stopping_rounds=50,
                          verbose_eval=0,
                          callbacks=[pruning_callback])
    trial.set_user_attr('best_iteration', xgb_model.best_iteration)
    #xgb.XGBClassifier(**params, random_state=46, early_stopping_rounds=30, objective='multi:softprob', lambda_=config['lam'], alpha=config['alpha'], n_estimators=100)
    #xgb_model.fit(X_train, Y_train, eval_set=[(X_train, Y_train), (X_valid, Y_valid)])

    y_pred = xgb_model.predict(dvalid)
    rmse_buy = mean_squared_error(y_valid['BuyPower'], y_pred[:, 0]) ** 0.5
    rmse_sell = mean_squared_error(y_valid['SellPower'], y_pred[:, 1]) ** 0.5

    return (rmse_buy + rmse_sell) / 2

In [27]:

study = optuna.create_study(direction='minimize') # for metric auc its maximuze, and for mlogloss its minimie

study.optimize(objective, n_trials=50)

# Get the best parameters
print(f" Best parameters: {study.best_params}")
print(f" Best Accuracy: {study.best_value}")

[I 2025-02-17 20:51:27,361] A new study created in memory with name: no-name-46f70707-8251-48b5-8d3e-a7cb3169bbd5
[I 2025-02-17 20:51:27,980] Trial 0 finished with value: 0.6515807970409899 and parameters: {'tree_method': 'hist', 'gamma': 3.7362769306983497, 'max_depth': 6, 'min_child_weight': 238.8393213289933, 'subsample': 0.5462703584348414, 'colsample_bytree': 0.5263556131898204, 'lambda': 9.55447526206348, 'alpha': 3.3594588041662807}. Best is trial 0 with value: 0.6515807970409899.
[I 2025-02-17 20:51:30,223] Trial 1 finished with value: 0.640617053879295 and parameters: {'tree_method': 'hist', 'gamma': 0.19007291839170387, 'max_depth': 11, 'min_child_weight': 21.97780189164064, 'subsample': 0.1311149284263565, 'colsample_bytree': 0.5043209909460648, 'lambda': 24.042288190202566, 'alpha': 1.7719395158227167}. Best is trial 1 with value: 0.640617053879295.
[I 2025-02-17 20:51:30,704] Trial 2 finished with value: 0.6838508819069682 and parameters: {'tree_method': 'approx', 'gamma':

 Best parameters: {'tree_method': 'hist', 'gamma': 0.05431158167659074, 'max_depth': 7, 'min_child_weight': 34.03945635179085, 'subsample': 0.7830486052063284, 'colsample_bytree': 0.9973947095597353, 'lambda': 8.80793358873873, 'alpha': 3.2665289666238464}
 Best Accuracy: 0.446780121283158


In [28]:
best_params = study.best_params
best_params

{'tree_method': 'hist',
 'gamma': 0.05431158167659074,
 'max_depth': 7,
 'min_child_weight': 34.03945635179085,
 'subsample': 0.7830486052063284,
 'colsample_bytree': 0.9973947095597353,
 'lambda': 8.80793358873873,
 'alpha': 3.2665289666238464}

In [47]:
low_learning_rate = 0.01

params = {}
params.update(base_params)
params.update(study.best_params)
params['learning_rate'] = low_learning_rate

model_stage2 = xgb.train(params=params, dtrain=dtrain, num_boost_round=num_boosting_rounds, 
                         evals=[(dtrain, 'train'), (dvalid, 'valid')], 
                         early_stopping_rounds=50,
                         verbose_eval=0)

In [49]:
model_stage2.best_iteration # got the best iteration from stage 2 training

9999

In [50]:
model_final = xgb.train(params=params, dtrain=dtrain_valid,
                        num_boost_round = model_stage2.best_iteration,
                        verbose_eval=0)

In [51]:
model_path = f'../{config['model_save_name']}'
model_final.save_model(model_path)

In [52]:
y_pred_test = model_final.predict(dtest)

y_pred_buy = y_pred_test[:, 0]

y_pred_sell = y_pred_test[:, 1]

metrics = {
    "RMSE (Buy Power)": mean_squared_error( y_test['BuyPower'], y_pred_buy),
    "RMSE (Sell Power)": mean_squared_error(y_test['SellPower'], y_pred_sell),
}

df_metrics = pd.DataFrame(metrics.items(), columns=["Metric", "Value"])

print(df_metrics)


              Metric     Value
0   RMSE (Buy Power)  0.157745
1  RMSE (Sell Power)  0.167617


In [53]:
## Load the new data to run inference
#new_data = pd.read_excel(config['data_excel_path'], sheet_name='TestNew')
new_data_start_date = pd.to_datetime(config['inf_start_date'])
new_data_end_date = pd.to_datetime(config['inf_end_date'])
new_data = all_trading_data[(all_trading_data['Date'] >= new_data_start_date) & (all_trading_data['Date'] <= new_data_end_date)]
new_data = new_data.reset_index(drop=True)

In [54]:
new_data.shape

(19395, 7)

In [55]:
bolband_period = config['bolband_period']
donchn_period = config['donchn_period']
max_MA_period = 100
max_EMA_period = 20
tchr_period = config['tchr_period']
adwm_period = config['adwm_period']
atr_period = config['atr_period']
volume_ma_period = config['volume_ma_period']
print(f" Fourier window : {fourier_lookback_window}")
max_window = max(bolband_period, 
                 donchn_period, 
                 max_MA_period, 
                 max_EMA_period,
                 tchr_period,
                 adwm_period,
                 atr_period,
                 volume_ma_period, fourier_lookback_window)


 Fourier window : 100


In [56]:
def process_data(raw_data):
    #### Loading the scalers for inferencing
    with open(f'../{config['robust_scaler_path']}', 'rb') as f:
        robust_scaler = pickle.load(f)

    # Load standard scaler
    with open(f'../{config['stand_scaler_path']}', 'rb') as f:
        stand_scaler = pickle.load(f)

    with open(f'../{config['fourier_minmax_path']}', 'rb') as f:
        fourier_minmax = pickle.load(f)

    with open(f'../{config['label_scales_pickle']}', 'rb') as f:
        label_scales = pickle.load(f)
    
    scalers = {'fourier_minmax': fourier_minmax, 
               'stand': stand_scaler,
               'robust': robust_scaler}

    trading_signals = pd.DataFrame(columns=['Date','High', 'Low', 'Open', 'Close', 'BuyPower', 'SellPower', 'Signal', 'Take_Profit_Level'])

                    
    # This is the dataframe to which we will be adding the rows live
    historical_data = pd.DataFrame(columns=['Date','High', 'Low', 'Open', 'Close', 'Volume'])
    numeric_columns = ['High', 'Low', 'Open', 'Close', 'Volume'] 
    historical_data[numeric_columns] = historical_data[numeric_columns].apply(pd.to_numeric)
    predictions = []
    for index,row in raw_data.iterrows():
        #print(f'volume : {row['Volume']}')
        if index % 100 == 0:
            print(f'Index : {index}')
        new_row = pd.DataFrame({'Date': [row['Date']], 'High': [row['High']], 'Low': [row['Low']], 'Open': [row['Open']], 'Close': [row['Close']], 'Volume': [row['Volume']]})
        signal_row = pd.DataFrame({'Date': [row['Date']], 'High': [row['High']], 'Low': [row['Low']], 'Open': [row['Open']], 'Close': [row['Close']], 'Signal': ['N']})
        trading_signals = pd.concat([trading_signals, signal_row], ignore_index=True)
        historical_data = pd.concat([historical_data, new_row], ignore_index=True)
        historical_data['Volume'] = historical_data['Volume'].astype(int)
        #print(historical_data['Volume'])
        #print(f'historical data length : {len(historical_data)}')
        if len(historical_data) > max_window:
            #print(f"At index : {index}")
            #print(f"length of historical data : {len(historical_data)} , so splicing")
            historical_data = historical_data.iloc[-max_window:].reset_index(drop=True)
            #print(f"Now lenngth : {len(historical_data)} and max window : {max_window}")
            
        if len(historical_data) >= max_window:
            updated_data = add_new_features_df(historical_data.copy())
            #print("Historical data 1 : ")
            #print(historical_data[['Volume']].tail())
            #last_row_to_print = historical_data.iloc[[-1]]
            #for column, value in last_row_to_print.items():
            #    print(f'{column} : {value}')
            #updated_data.info()
            inf_features = get_features(updated_data.copy(), inference=True, scalers=scalers)
            #print("Historical data 2 : ")
            #print(historical_data[['Volume']].tail())
            last_row_features = inf_features.iloc[[-1]]
            last_row_features = last_row_features[all_feature_columns]
            if last_row_features.isna().any().any():
                print(f'The inference row at index : {index} contains na')
                #last_row_to_print = updated_data.iloc[[-1]]
                #for column, value in last_row_to_print.items():
                #    print(f'{column} : {value}')
                print(historical_data[['Volume']].tail())
                break
                continue
        
            last_row_dm = xgb.DMatrix(last_row_features, enable_categorical=True)
            prediction = model_final.predict(last_row_dm)
 
            buy_power, sell_power = prediction[0]
            if config['label_power_transform']:
                pred_df = pd.DataFrame([[buy_power, sell_power]], columns=['BuyPower', 'SellPower'])
                pred_original_df = pd.DataFrame(label_scales['PT'].inverse_transform(pred_df), columns=pred_df.columns)
                buy_power = pred_original_df['BuyPower'].iloc[0]
                sell_power = pred_original_df['SellPower'].iloc[0]
            #print(f'Buy Power : {buy_power}, Sell Power : {sell_power}')

            #predicted_class_index = np.argmax(prob_prediction, axis=1)
            trading_signals.loc[trading_signals.index[-1], 'BuyPower'] = buy_power
            trading_signals.loc[trading_signals.index[-1], 'SellPower'] = sell_power
            trading_signals.loc[trading_signals.index[-1], 'Take_Profit_Level'] = updated_data['Take_Profit_Level'].iloc[-1]
            #predictions.append(prediction[0])
        
        
    return trading_signals

            

        
    

In [57]:
def calculate_trade(trading_signals):
    trade_positions = []
    trade_enter_buy = config['trade_enter_buy']
    trade_enter_sell = config['trade_enter_sell']
    trades = []
    balance = 0
    profit_amount = 10
    profit_count = 0
    loss_count = 0
    buy_count = 0
    sell_count = 0
    loss_amount = profit_amount * config['risk']
    positions = pd.DataFrame(columns=['Entry', 'EntryDate', 'Exit', 'ExitDate', 'Profit', 'Type'])
                    
    for index,row in trading_signals.iterrows():
        buy_power = row['BuyPower']
        sell_power = row['SellPower']
        #print(f'Buy Power : {buy_power}, Sell Power : {sell_power}')

        #predicted_class_index = np.argmax(prob_prediction, axis=1)          #predictions.append(prediction[0])
        for trade in trades:
            if (trade['Type'] == 'B' and row['High'] >= trade['TakeProfit']) or (trade['Type'] == 'S' and row['Low'] <= trade['TakeProfit']):
                trade['Active'] = 'N'
                balance += (trade['Profit'] * profit_amount)
                profit_count += 1
                print(f"Profit, New Balance : {balance}")
                
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [True], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)
            elif (trade['Type'] == 'B' and row['Low'] <= trade['StopLoss']) or (trade['Type'] == 'S' and row['High'] >= trade['StopLoss']):
                trade['Active'] = 'N'
                balance -= (trade['Profit'] * loss_amount)
                loss_count += 1
                print(f"Loss, New Balance : {balance}")
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [False], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)
        
        
        if len(trades) == 0:
            if buy_power > sell_power and buy_power > trade_enter_buy:
                take_profit = row['Take_Profit_Level'] 
                trades.append({"Type": "B", 
                            "TakeProfit": row['Close'] + take_profit,
                            "StopLoss": row['Close'] - (take_profit * config['risk']),
                            "Profit": take_profit,
                            "Active": "Y",
                            'Entry': row['Close'],
                            'EntryDate': row['Date']
                            })
                buy_count += 1
            elif sell_power > buy_power and sell_power > trade_enter_sell:
                take_profit = row['Take_Profit_Level'] 
                trades.append({"Type": "S", 
                            "TakeProfit": row['Close'] - take_profit,
                            "Profit": take_profit,
                            "StopLoss": row['Close'] + (take_profit * config['risk']),
                            "Active": "Y",
                            'Entry': row['Close'],
                            'EntryDate': row['Date']
                            })
                sell_count += 1
        else:
            if buy_power > sell_power and buy_power > trade_enter_buy and trades[0]['Type'] == 'S':
                trade['Active'] = 'N'
                profit = (trade['Entry'] - row['Close']) * profit_amount
                balance += profit 
                if profit < 0:
                    loss_count += 1
                    print(f"Loss, New Balance : {balance}")
                else:
                    profit_count += 1
                    print(f"Profit, New Balance : {balance}")
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [True] if profit > 0 else [False], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)

            elif sell_power > buy_power and sell_power > trade_enter_sell and trades[0]['Type'] == 'B':
                trade['Active'] = 'N'
                profit = (row['Close'] - trade['Entry']) * profit_amount
                balance += profit
                if profit < 0:
                    loss_count += 1
                    print(f"Loss, New Balance : {balance}")
                else:
                    profit_count += 1
                    print(f"Profit, New Balance : {balance}")
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [True] if profit > 0 else [False], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)
            
        # Filter out all trades that are not active
        trades = [trade for trade in trades if trade['Active'] == 'Y']
        
        
    print(f"Final Balance : {balance} \n Profit count : {profit_count} \n Loss count : {loss_count}")
    print(f"Buy count : {buy_count} \n Sell count : {sell_count}")
    
    return positions

            

        
    

In [58]:
new_data.isna().any(axis=1).sum()

np.int64(0)

In [59]:
print(volume_ma_period)

10


In [60]:
new_data.head()

Date Symbol     Open    High     Low   Close   Volume
0 2024-01-02 09:30:00    SPY  472.160  472.80  472.05  472.67  2339778
1 2024-01-02 09:35:00    SPY  472.670  472.74  471.88  471.92  1574945
2 2024-01-02 09:40:00    SPY  471.920  472.10  471.71  471.80  1634708
3 2024-01-02 09:45:00    SPY  471.790  472.09  471.39  471.39  1398881
4 2024-01-02 09:50:00    SPY  471.395  471.95  471.36  471.42  1396561

In [61]:
tr_signals = process_data(new_data)


Index : 0
Index : 100


/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17467/3331053336.py:34: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.

/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17467/3331053336.py:35: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



Index : 200
Index : 300
Index : 400
Index : 500
Index : 600
Index : 700
Index : 800
Index : 900
Index : 1000
Index : 1100
Index : 1200
Index : 1300
Index : 1400
Index : 1500
Index : 1600
Index : 1700
Index : 1800
Index : 1900
Index : 2000
Index : 2100
Index : 2200
Index : 2300
Index : 2400
Index : 2500
Index : 2600
Index : 2700
Index : 2800
Index : 2900
Index : 3000
Index : 3100
Index : 3200
Index : 3300
Index : 3400
Index : 3500
Index : 3600
Index : 3700
Index : 3800
Index : 3900
Index : 4000
Index : 4100
Index : 4200
Index : 4300
Index : 4400
Index : 4500
Index : 4600
Index : 4700
Index : 4800
Index : 4900
Index : 5000
Index : 5100
Index : 5200
Index : 5300
Index : 5400
Index : 5500
Index : 5600
Index : 5700
Index : 5800
Index : 5900
Index : 6000
Index : 6100
Index : 6200
Index : 6300
Index : 6400
Index : 6500
Index : 6600
Index : 6700
Index : 6800
Index : 6900
Index : 7000
Index : 7100
Index : 7200
Index : 7300
Index : 7400
Index : 7500
Index : 7600
Index : 7700
Index : 7800
Index :

In [62]:
tr_signals.head()

Date    High     Low     Open   Close BuyPower SellPower  \
0 2024-01-02 09:30:00  472.80  472.05  472.160  472.67      NaN       NaN   
1 2024-01-02 09:35:00  472.74  471.88  472.670  471.92      NaN       NaN   
2 2024-01-02 09:40:00  472.10  471.71  471.920  471.80      NaN       NaN   
3 2024-01-02 09:45:00  472.09  471.39  471.790  471.39      NaN       NaN   
4 2024-01-02 09:50:00  471.95  471.36  471.395  471.42      NaN       NaN   

  Signal Take_Profit_Level  
0      N               NaN  
1      N               NaN  
2      N               NaN  
3      N               NaN  
4      N               NaN

In [63]:
positions_df = calculate_trade(tr_signals.copy())
#tr_signals.tail()

Loss, New Balance : -19.38870772475091
Profit, New Balance : -7.738707724751272
Loss, New Balance : -24.36778290068512
Profit, New Balance : 9.63221709931522
Loss, New Balance : -5.017160079840352
Loss, New Balance : -18.54060301104084
Profit, New Balance : 11.2498251807808
Profit, New Balance : 48.30457349812136
Profit, New Balance : 94.44699608775608
Loss, New Balance : 92.5469960877561
Loss, New Balance : 87.8469960877564
Loss, New Balance : 68.6989896471341
Profit, New Balance : 92.8489896471343
Loss, New Balance : 90.84898964713442
Loss, New Balance : 65.87727008241708
Loss, New Balance : 46.068923037408474
Loss, New Balance : 23.14748869471002
Profit, New Balance : 37.047488694709884
Loss, New Balance : 35.19748869470986
Profit, New Balance : 64.16473850614344
Loss, New Balance : 63.96473850614362
Loss, New Balance : 40.59288128532363
Profit, New Balance : 95.36842243505029
Profit, New Balance : 149.96842243505066
Loss, New Balance : 127.50616365704826
Profit, New Balance : 139.8

/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17467/1740360933.py:36: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



In [64]:
def compute_trade_signal(row):
    if row['BuyPower'] > config['trade_enter_buy'] and row['BuyPower'] > row['SellPower']:
        return 'B'
    elif row['SellPower'] > config['trade_enter_sell'] and row['SellPower'] > row['BuyPower']:
        return 'S'
    else:
        return 'N'
    
tr_signals['Signal'] = tr_signals.apply(compute_trade_signal, axis=1)

In [46]:
buy_signals = tr_signals[tr_signals['Signal'] == 'B']
sell_signals = tr_signals[tr_signals['Signal']== 'S']
#trading_data['Date'] = pd.to_datetime(trading_data['Date'])
fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                    row_heights=[0.7, 0.3], vertical_spacing=0.1,
                    subplot_titles=("CandleStick Chart", "Buy/Sell Signals"))
fig.add_trace(
    go.Candlestick(
        x=tr_signals['Date'], 
        open=tr_signals['Open'], 
        high=tr_signals['High'], 
        low=tr_signals['Low'], 
        close=tr_signals['Close'],
        name='OHLC'
        ), row=1, col=1
)
'''
fig.add_trace(
    go.Scatter(
        x=buy_signals['Date'], 
        y=buy_signals['Low'], 
        mode='markers', 
        name='Buy Signal', 
        marker=dict(color='blue', size=10)))

fig.add_trace(
    go.Scatter(
        x=sell_signals['Date'], 
        y=sell_signals['High'], 
        mode='markers', 
        name='Sell Signal', 
        marker=dict(color='yellow', size=10)))
'''
for index, row in positions_df.iterrows():
    if row['Type'] == 'B':
        entry_symbol = 'triangle-up'
        entry_color = 'blue'
        exit_symbol = 'triangle-down'
        exit_color ='green' if row['Profit'] else 'red'
    elif row['Type'] == 'S':
        entry_symbol = 'triangle-down'
        entry_color = 'yellow'
        exit_symbol = 'triangle-up'
        exit_color = 'green' if row['Profit'] else 'red'
    
    fig.add_trace(
        go.Scatter(
            x=[row['EntryDate']],
            y=[row['Entry']],
            mode='markers',
            marker=dict(symbol=entry_symbol, size=10, color=entry_color),
            name=f'Entry {row['Type']}'
        ))
    
    fig.add_trace(
        go.Scatter(
            x=[row['ExitDate']],
            y=[row['Exit']],
            mode='markers',
            marker=dict(symbol=exit_symbol, size=10, color=exit_color),
            name=f'Exit {row["Type"]}'
        ))
    
fig.add_trace(
    go.Scatter(
        x=tr_signals['Date'],
        y=tr_signals['BuyPower'],
        mode='lines',
        name='Buy Signal',
        line=dict(color='green', width=2)
    ), row=2, col=1
)

fig.add_trace(
    go.Scatter(
        x=tr_signals['Date'],
        y=tr_signals['SellPower'],
        mode='lines',
        name='Sell Signal',
        line=dict(color='red', width=2)
    ), row=2, col=1
)
   

fig.update_layout(
    title='CandleStick chart with Buy Sell Signals',
    xaxis=dict(type="date", 
               rangebreaks=[
                   dict(bounds=["sat", "mon"]),
                   dict(bounds=[16,9.5], pattern='hour')
               ]              
            ),
    xaxis_rangeslider_visible=False,
    height=600,
    hovermode='x unified'
)



fig.update_xaxes(matches='x')

fig.show()